In [1]:
#import function from part1
%run Part_1.ipynb

#import function from part2
%run Part_2.ipynb

Word: Estuvimos, Label: O
Word: hace, Label: O
Word: poco, Label: O
Word: mi, Label: O
Word: pareja, Label: O
Word: y, Label: O
Word: yo, Label: O
Word: comiendo, Label: O
Word: y, Label: O
Word: resultó, Label: O
Word: todo, Label: O
Word: muy, Label: O
Word: bien, Label: O
Word: ,, Label: O
Word: tanto, Label: O
Word: la, Label: O
Word: comida, Label: B-positive
Word: ,, Label: O
Word: el, Label: O
Word: vino, Label: B-positive
Word: ,, Label: O
Word: el, Label: O
Word: trato, Label: B-positive
Word: ,, Label: O
Word: la, Label: O
Word: decoración, Label: B-positive
Word: …, Label: O
Word: nos, Label: O
Word: gustó, Label: O
Word: todo, Label: O
Word: mucho, Label: O
Word: ., Label: O

Word: Por, Label: O
Word: poner, Label: O
Word: algún, Label: O
Word: pero, Label: O
Word: ,, Label: O
Word: quizá, Label: O
Word: el, Label: O
Word: jamón, Label: B-negative
Word: no, Label: O
Word: era, Label: O
Word: todo, Label: O
Word: lo, Label: O
Word: ", Label: O
Word: ibérico, Label: O
Word: "

In [2]:
#Estimates the transition parameters from the training set using MLE
def estimate_transition_data(training_data):
    transition_counts={}
    tags_counts={}
    for sentence in training_data:

        start_tag = sentence[0][1]
        transition_counts[('start', start_tag)] = transition_counts.get(('start', start_tag), 0) + 1
        tags_counts['start'] = tags_counts.get('start', 0) + 1
        
        stop_tag=sentence[-1][1]
        transition_counts[(stop_tag, 'stop')] = transition_counts.get((stop_tag, 'stop'), 0) + 1
        tags_counts[stop_tag] = tags_counts.get(stop_tag, 0) + 1

        for i in range(0,len(sentence)-1):
            first_tag,second_tag = sentence[i][1],sentence[i+1][1]
            transition_counts[(first_tag, second_tag)] = transition_counts.get((first_tag, second_tag), 0) + 1
            tags_counts[first_tag] = tags_counts.get(first_tag, 0) + 1
    
    transition_parameters={}
    for (first,second), count in transition_counts.items():
        tags_count = tags_counts[first]
        transition_parameters[(first,second)]=count/tags_count

    return transition_parameters

transition_parameters = estimate_transition_data(training_data)

for (first, second), param in transition_parameters.items():
    
    print(f"First: {first}, Second: {second}, Transition Parameter: {param:.4f}")

First: start, Second: O, Transition Parameter: 0.9289
First: O, Second: stop, Transition Parameter: 0.0634
First: O, Second: O, Transition Parameter: 0.8857
First: O, Second: B-positive, Transition Parameter: 0.0365
First: B-positive, Second: O, Transition Parameter: 0.8716
First: O, Second: B-negative, Transition Parameter: 0.0122
First: B-negative, Second: O, Transition Parameter: 0.8110
First: start, Second: B-positive, Transition Parameter: 0.0522
First: O, Second: B-neutral, Transition Parameter: 0.0021
First: B-neutral, Second: I-neutral, Transition Parameter: 0.2083
First: I-neutral, Second: I-neutral, Transition Parameter: 0.6512
First: I-neutral, Second: O, Transition Parameter: 0.3488
First: B-positive, Second: I-positive, Transition Parameter: 0.1164
First: I-positive, Second: I-positive, Transition Parameter: 0.5701
First: I-positive, Second: O, Transition Parameter: 0.4268
First: B-neutral, Second: O, Transition Parameter: 0.7917
First: B-negative, Second: I-negative, Tran

In [3]:
# def k_best_viterbi(sentences, tags, trans_prob, emit_prob, k):
#     n = len(sentences)
#     count_tags = len(tags)

#     # Initialize the data structure to maintain top-k sequences at each timestep
#     top_k_sequences = [{} for _ in range(n + 1)]
#     # top_k_sequences[0]['start'] = [(1.0, ['start'])]

#     # Loop through each timestep
#     for i in range(n):
#         for u in tags:
#             max_k_probabilities = []
#             if i == 0:
#                 prev_prob = 1.0
#             else:
#                 prev_prob = top_k_sequences[i][u][0][0]  # Use 'u' instead of 'v'
#             for v in tags:
#                 trans = trans_prob.get((v, u), 0.0)
#                 emit = emit_prob.get((sentences[i], u), 0.0)
#                 prob = prev_prob * trans * emit
#                 # Keep track of top-k transitions

#                 for (prob_v, path_v) in top_k_sequences[i][v]:
#                     max_k_probabilities.append((prob_v * prob, path_v + [u]))
#             # Select the top-k transitions for state u at timestep i
#             max_k_probabilities.sort(reverse=True)
#             top_k_sequences[i + 1][u] = max_k_probabilities[:k]


#     print(max_k_probabilities)

#     print(top_k_sequences)
#     # print(tags)

#     return kth_best_sequence


In [4]:
def k_best_sequences(sentences, tags, trans_prob, emit_prob, k):
    n = len(sentences)
    count_tags = len(tags)

    # Initialize a list to store all sequences at each timestep
    all_sequences_list = [{} for _ in range(n + 1)]
    all_sequences_list[0]["start"] = [([], 1.0)]  # Initial starting state

    # Dynamic programming to find all sequences
    for i in range(n):
        all_sequences_list[i + 1] = {}
        for u in tags:
            all_sequences_list[i + 1][u] = []
            for seq, prob in all_sequences_list[i].get(u, []):  # Use .get() to handle missing tags
                max_prob = -1
                max_prev_tag = None
                for v in tags:
                    prev_prob = prob
                    trans = trans_prob.get((v, u), 1e-10)  # Handle zero probability transitions
                    emit = emit_prob.get((sentences[i], u), 0.0)
                    prob = prev_prob * trans * emit
                    
                    print(f"i: {i}, u: {u}, v: {v}, seq: {seq}, prob: {prob:.6f}, trans: {trans:.6f}, emit: {emit:.6f}")

                    if prob > max_prob:
                        max_prob = prob
                        max_prev_tag = v

                new_seq = seq + [u]
                all_sequences_list[i + 1][u].append((new_seq, max_prob))

    # Final Step: Find the k-th best sequences by ranking and selecting top-k
    ranked_sequences = []
    for v in tags:
        for seq, prob in all_sequences_list[n].get(v, []):
            if seq:  # Check if the sequence is non-empty
                ranked_sequences.append((seq, prob))
    ranked_sequences.sort(reverse=True, key=lambda x: x[1])
    k_best_output_sequences = [seq for seq, _ in ranked_sequences[:k]]

    return k_best_output_sequences


In [5]:
es_train_path = 'Data/ES/train'
ru_train_path = 'Data/RU/train'

es_training_data = read_training_data(es_train_path)
ru_training_data = read_training_data(ru_train_path)

es_emission_parameters = estimate_emission_parameters(es_training_data,k)
ru_emission_parameters = estimate_emission_parameters(ru_training_data,k)

es_transition_parameters = estimate_transition_data(es_training_data)
# Add ('start', 'O') transition with an initial count of 0
# es_transition_parameters[('start', 'O')] = 0.0


ru_transition_parameters = estimate_transition_data(ru_training_data)

for (first, second), param in es_transition_parameters.items():
    
    print(f"First: {first}, Second: {second}, Transition Parameter: {param:.4f}")



First: start, Second: O, Transition Parameter: 0.9289
First: O, Second: stop, Transition Parameter: 0.0634
First: O, Second: O, Transition Parameter: 0.8857
First: O, Second: B-positive, Transition Parameter: 0.0365
First: B-positive, Second: O, Transition Parameter: 0.8716
First: O, Second: B-negative, Transition Parameter: 0.0122
First: B-negative, Second: O, Transition Parameter: 0.8110
First: start, Second: B-positive, Transition Parameter: 0.0522
First: O, Second: B-neutral, Transition Parameter: 0.0021
First: B-neutral, Second: I-neutral, Transition Parameter: 0.2083
First: I-neutral, Second: I-neutral, Transition Parameter: 0.6512
First: I-neutral, Second: O, Transition Parameter: 0.3488
First: B-positive, Second: I-positive, Transition Parameter: 0.1164
First: I-positive, Second: I-positive, Transition Parameter: 0.5701
First: I-positive, Second: O, Transition Parameter: 0.4268
First: B-neutral, Second: O, Transition Parameter: 0.7917
First: B-negative, Second: I-negative, Tran

In [6]:
# def read_gold_standard_outputs(file_path):
#     gold_standard_outputs = []
#     with open(file_path, 'r') as f:
#         sentence = []
#         for line in f:
#             line = line.strip()
#             if line:
#                 word, label = line.split('\t')  # Assuming the word and label are separated by a tab
#                 sentence.append(label)
#             else:
#                 gold_standard_outputs.append(sentence)
#                 sentence = []
#         if sentence:
#             gold_standard_outputs.append(sentence)  # Add the last sentence if it's not empty
#     return gold_standard_outputs


In [8]:
k = 8  # Change this to the desired k value
es_dev_in = read_dev_in('Data/ES/dev.in')  # Read input sentences
ru_dev_in = read_dev_in('Data/RU/dev.in')

es_k_best_sequences = []
ru_k_best_sequences = []

for sentences in es_dev_in:
    k_best_seqs = k_best_sequences(sentences, es_tags, es_transition_parameters, es_emission_parameters, k)
    es_k_best_sequences.append(k_best_seqs)
    print("K-Best Sequences for ES:")
    for i, seqs in enumerate(es_k_best_sequences):
        print(f"Sequence {i}: {seqs}")



for sentences in ru_dev_in:
    k_best_seqs = k_best_sequences(sentences, ru_tags, ru_transition_parameters, ru_emission_parameters, k)
    ru_k_best_sequences.append(k_best_seqs)



    
# Write k-th best outputs to files
def write_k_best_outputs_to_file(output_sequences, file_path):
    with open(file_path, 'w') as f:
        for seqs in output_sequences:
            for seq in seqs:
                f.write(" ".join(seq) + "\n")
            f.write("\n")

write_k_best_outputs_to_file(es_k_best_sequences, 'Data/ES/dev.p3.8th.out')
write_k_best_outputs_to_file(ru_k_best_sequences, 'Data/RU/dev.p3.8th.out')

# Read gold-standard outputs
es_gold_standard_outputs = read_gold_standard_outputs('Data/ES/dev.out')
ru_gold_standard_outputs = read_gold_standard_outputs('Data/RU/dev.out')

# Calculate scores for ES dataset
print("Length of predicted sequences:", len(es_k_best_sequences))
print("Length of gold standard sequences:", len(es_gold_standard_outputs))

# for gold_sentence in es_gold_standard_outputs:
#     print("Gold Sentence:", gold_sentence)
# es_k_best_precision, es_k_best_recall, es_k_best_f_score = calculate_scores(es_k_best_sequences, es_gold_standard_outputs)
# ru_k_best_precision, ru_k_best_recall, ru_k_best_f_score = calculate_scores(ru_k_best_sequences, ru_gold_standard_outputs)

# print("For ES Dataset (8th Best):")
# print(f"Precision: {es_k_best_precision:.2f}")
# print(f"Recall: {es_k_best_recall:.2f}")
# print(f"F-score: {es_k_best_f_score:.2f}")

# print("For RU Dataset (8th Best):")
# print(f"Precision: {ru_k_best_precision:.2f}")
# print(f"Recall: {ru_k_best_recall:.2f}")
# print(f"F-score: {ru_k_best_f_score:.2f}")

K-Best Sequences for ES:
Sequence 0: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
Sequence 2: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
Sequence 2: []
Sequence 3: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
Sequence 2: []
Sequence 3: []
Sequence 4: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
Sequence 2: []
Sequence 3: []
Sequence 4: []
Sequence 5: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
Sequence 2: []
Sequence 3: []
Sequence 4: []
Sequence 5: []
Sequence 6: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
Sequence 2: []
Sequence 3: []
Sequence 4: []
Sequence 5: []
Sequence 6: []
Sequence 7: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
Sequence 2: []
Sequence 3: []
Sequence 4: []
Sequence 5: []
Sequence 6: []
Sequence 7: []
Sequence 8: []
K-Best Sequences for ES:
Sequence 0: []
Sequence 1: []
Sequence 2: []
Sequence 3: []
Sequence 4: []
